In [1]:
import os

os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = 'C:\\STUDY\\2023-High-Light-SolutionChallenge\\vision_api_key.json'


In [9]:
!pip install --upgrade google-cloud-vision


[notice] A new release of pip available: 22.3.1 -> 23.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
import io
import os

# Imports the Google Cloud client library
from google.cloud import vision

# Instantiates a client
client = vision.ImageAnnotatorClient()

# The name of the image file to annotate
file_name = os.path.abspath(
    'C:\\STUDY\\2023-High-Light-SolutionChallenge\\Vision-API\\temp_dataset\\person.png')

# Loads the image into memory
with io.open(file_name, 'rb') as image_file:
    content = image_file.read()

image = vision.Image(content=content)

# Performs label detection on the image file
response = client.label_detection(image=image)
labels = response.label_annotations

print('Labels:')
for label in labels:
    print(label.description)


Labels:
Chin
Eyebrow
Gesture
Tie
Font
Happy
Suit
Eyelash
Formal wear
Photo caption


### 이미지에서 텍스트 추출

In [12]:
def detect_text(path):
    """Detects text in the file."""
    from google.cloud import vision
    import io
    # 인증 key 입력
    BASE_DIR = 'private'
    os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = os.path.join(
        BASE_DIR, "C:\\STUDY\\2023-High-Light-SolutionChallenge\\vision_api_key.json")
    # Vision API에 액세스
    client = vision.ImageAnnotatorClient()

    with io.open(path, 'rb') as image_file:
        content = image_file.read()

    image = vision.Image(content=content)

    # response -> json 파일 형태(text, 각 단어별 위치 존재)
    response = client.text_detection(image=image)
    texts = response.text_annotations
    text_list = list(map(lambda x: x.description, texts))

    # 에러 처리
    if response.error.message:
        raise Exception(
            '{}\nFor more info on error messages, check: '
            'https://cloud.google.com/apis/design/errors'.format(
                response.error.message))

    return text_list


In [13]:
text = detect_text(
    'C:\\STUDY\\2023-High-Light-SolutionChallenge\\Vision-API\\temp_dataset\\temp.png')
print(text)


["4.3 확대 모드 및 음성 모드 기능\n확대 모드 실행 시, 선택 모드에서 추가한 이벤트\n리스너를 삭제하고 200m(확대모드) 또는 zoomtts\n(확대음성모드)를 매개변수로 JS의 startZoom 함수\n를 호출한다. JS의 객체 배열의 데이터를 dovu-\nment.write 하고, 전달 받은 모드가 zoomtts라면 음\n성 모드를 실행한다.\n음성 모드 실행 시, 선택 모드에서 추가한 이벤트\n리스너를 삭제한다. JS의 객체 배열을 매개변수로\nJavascriptInterface의 speech 함수를 호출한다.\nspeech 함수에서 띄어쓰기 부분에서 자연스럽게 끊\n어 읽을 수 있도록 휴지기 처리를 한다. 처리된 문장\n을 TTS speak()한다. 다음 Fig. 6는 확대 모드 및\n음성 모드의 실행 화면이다.\nROM GOOD\n홈페이지 주소를 입력하세요 Q. ★ 시작\n940\n우리 대학의 중장\n기 발전계획의 일\n환인 '학생의 행복\n과 성장을 지원하\n는 WISE 교육혁\n신모델 구현'을\n목표로 학생의 자\n기주도성장을 지\n원하는 유연한 학\n사제도를 운영하\n고자 함\n640\n주소입력하세요\n반복 0\n속도\nMagnification Mode Control Screen\nFig. 6. Screenshot of Magnification and Audion Output\nFunction.\nVoice Mode Control Screen\n저시력자를 위한 모바일 보이스 웹 브라우저 개발 1423\n다. 이때, JavascriptInterface에 저장한 객체 클래스\n를 불러와 JS의 객체 배열에 추가하고, 하이라이트\n스타일을 적용한다. 세팅이 완료되면 initChoice 함\n수를 실행하고 음성합성 객체가 남아있다면 실행을\n중지하고 메모리에서 제거한다.\n모드 취소(cancel)는 선택한 모든 데이터가 삭제\n되고 초기화되어야 한다. 우선 음성합성 객체가 남아\n있다면 실행을 중지하고 메모리에서 제거한다. 선택\n모드에서 추

### 추출한 텍스트 시각화

In [16]:
import argparse # 입력 파일 이름을 인수로 받을 수 있다.
from enum import Enum # FeatureType 열거에 사용
import io

from google.cloud import vision
from PIL import Image, ImageDraw

In [33]:
class FeatureType(Enum):
    PAGE = 1
    BLOCK = 2
    PARA = 3
    WORD = 4
    SYMBOL = 5

# text 부분을 bounding box 그리기
# bounds -> get_document_bounds를 통해서 좌표값 get
def draw_boxes(image, bounds, color):
    """Draw a border around the image using the hints in the vector list."""
    draw = ImageDraw.Draw(image)

    for bound in bounds:
        draw.polygon(
            [
                bound.vertices[0].x,
                bound.vertices[0].y,
                bound.vertices[1].x,
                bound.vertices[1].y,
                bound.vertices[2].x,
                bound.vertices[2].y,
                bound.vertices[3].x,
                bound.vertices[3].y,
            ],
            None,
            color,
        )
    return image

def get_document_bounds(image_file, feature):
    client = vision.ImageAnnotatorClient()
    
    bounds = []
    
    with io.open(image_file, 'rb') as image_file:
        content = image_file.read()
        
    image = vision.Image(content=content)
    
    response = client.document_text_detection(image=image)
    document = response.full_text_annotation
    print("document")
    print(document)
    
    # Collect specified feature bounds by enumerating all document features
    for page in document.pages:
        for block in page.blocks:
            for paragraph in block.paragraphs:
                for word in paragraph.words:
                    for symbol in word.symbols:
                        if feature == FeatureType.SYMBOL:
                            bounds.append(symbol.bounding_box)
                    if feature == FeatureType.WORD:
                        bounds.append(word.bounding_box)
                if feature == FeatureType.PARA:
                    bounds.append(paragraph.bounding_box)
            if feature == FeatureType.BLOCK:
                bounds.append(block.bounding_box)
    return bounds

def render_doc_text(filein, fileout):
    image = Image.open(filein)
    # bounds = get_document_bounds(filein, FeatureType.BLOCK)
    # draw_boxes(image, bounds, "blue")
    
    bounds = get_document_bounds(filein, FeatureType.PARA)
    draw_boxes(image, bounds, "red")
    
    # bounds = get_document_bounds(filein, FeatureType.WORD)
    # draw_boxes(image, bounds, "yellow")
    
    if fileout != 0:
        image.save(fileout)
    else:
        image.show()


In [30]:
# parser = argparse.ArgumentParser()
# parser.add_argument("detect_file", help='The image for text detection.')
# parser.add_argument("-out_file", help='Optional output file', default=0)
# args = parser.parse_args()

# render_doc_text(args.detect_file, args.out_file)
render_doc_text('temp_dataset/temp.png', 'temp_dataset/outTemp.png')


document
pages {
  property {
    detected_languages {
      language_code: "ko"
      confidence: 0.889205694
    }
    detected_languages {
      language_code: "en"
      confidence: 0.100371286
    }
  }
  width: 1146
  height: 1077
  blocks {
    bounding_box {
      vertices {
        x: 39
        y: 77
      }
      vertices {
        x: 529
        y: 77
      }
      vertices {
        x: 529
        y: 312
      }
      vertices {
        x: 39
        y: 312
      }
    }
    paragraphs {
      bounding_box {
        vertices {
          x: 40
          y: 77
        }
        vertices {
          x: 361
          y: 77
        }
        vertices {
          x: 361
          y: 97
        }
        vertices {
          x: 40
          y: 97
        }
      }
      words {
        property {
          detected_languages {
            language_code: "ko"
            confidence: 1
          }
        }
        bounding_box {
          vertices {
            x: 40
            y

In [34]:
render_doc_text('temp_dataset/temp.png', 'temp_dataset/outBlue.png')
# render_doc_text('temp_dataset/temp.png', 'temp_dataset/outRed.png')


document
pages {
  property {
    detected_languages {
      language_code: "ko"
      confidence: 0.889205694
    }
    detected_languages {
      language_code: "en"
      confidence: 0.100371286
    }
  }
  width: 1146
  height: 1077
  blocks {
    bounding_box {
      vertices {
        x: 39
        y: 77
      }
      vertices {
        x: 529
        y: 77
      }
      vertices {
        x: 529
        y: 312
      }
      vertices {
        x: 39
        y: 312
      }
    }
    paragraphs {
      bounding_box {
        vertices {
          x: 40
          y: 77
        }
        vertices {
          x: 361
          y: 77
        }
        vertices {
          x: 361
          y: 97
        }
        vertices {
          x: 40
          y: 97
        }
      }
      words {
        property {
          detected_languages {
            language_code: "ko"
            confidence: 1
          }
        }
        bounding_box {
          vertices {
            x: 40
            y

#### 문단의 기준을 파란색으로 하는게 좋은지, 빨간색으로 하는게 좋은지

-> 빨간색이 좋을듯

### 텍스트 추출을 문장별로 할 수 있는지

## 이미지 구분을 우선적으로 ***
## ppt를 예시로 해보면 좋을 듯
## 제목이랑 본문 구분 가능한지